In [1]:

import json
import os
import torch
torch.backends.cudnn.enabled = True
torch.backends.cudnn.benchmark = False
from torch.cuda import amp
from torch.utils.tensorboard import SummaryWriter
%load_ext autoreload
%autoreload 2 
# import radtts
import os
import json
from timeit import default_timer as timer
os.chdir('/usr/src/app/radtts')
from distributed import (init_distributed, apply_gradient_allreduce,
                         reduce_tensor)

In [2]:

from radtts import RADTTS
from train import RADTTSLoss, AttentionBinarizationLoss, prepare_dataloaders, prepare_model_weights, parse_data_from_batch, compute_validation_loss
import torch
# from radtts.inference import load_vocoder
from hifigan_env import AttrDict
from data import Data
from hifigan_models import Generator
from hifigan_env import AttrDict
from hifigan_denoiser import Denoiser
from radam import RAdam
torch.cuda.set_device(1)

# Needs to be here cause of implicit "config" argument
def prepare_output_folders_and_logger(output_directory):
    # Get shared output_directory ready
    if not os.path.isdir(output_directory):
        os.makedirs(output_directory)
        os.chmod(output_directory, 0o775)
        print("output directory", output_directory)

    output_config_path = os.path.join(output_directory, 'config.json')
    print("saving current configuration in output dir")
    config_fp = open(output_config_path, 'w')
    json.dump(config, config_fp, indent=4)
    config_fp.close()
    output_code_path = os.path.join(output_directory, 'code.tar.gz')
    os.system('tar -czvf %s *.py' % (output_code_path))

    tboard_out_path = os.path.join(output_directory, 'logs')
    print("setting up tboard log in %s" % (tboard_out_path))
    logger = SummaryWriter(tboard_out_path)
    return logger



In [3]:
config_path = '/usr/src/app/radtts/configs/lj_minimal.json'
config_path = '/usr/src/app/radtts/configs/config_ljs_radtts_ljdebug.json'
with open(config_path) as f:
    config = json.load(f)
seed = 1234

torch.manual_seed(seed)
torch.cuda.manual_seed(seed)
n_gpus = 1
train_config = config['train_config']
sigma = train_config['sigma']
model_config = config['model_config']
loss_weights = train_config['loss_weights']
learning_rate = train_config['learning_rate']
unfreeze_modules = train_config['unfreeze_modules']
weight_decay = train_config['weight_decay']
output_directory = train_config['output_directory']
use_amp = train_config['use_amp']
batch_size = train_config['batch_size']
iters_per_checkpoint = train_config['iters_per_checkpoint']
grad_clip_val = train_config['grad_clip_val']
data_config= config['data_config']
epochs =train_config['epochs']
binarization_start_iter = train_config['binarization_start_iter']
criterion = RADTTSLoss(
    sigma,
    model_config['n_group_size'],
    model_config['dur_model_config'],
    model_config['f0_model_config'],
    model_config['energy_model_config'],
    vpred_model_config=model_config['v_model_config'],
    loss_weights=loss_weights
)
attention_kl_loss = AttentionBinarizationLoss()
model = RADTTS(**model_config).cuda()
rank = 0


Applying spectral norm to text encoder LSTM
Applying spectral norm to context encoder LSTM


/usr/src/app/radtts/common.py:391: UserWarning: torch.qr is deprecated in favor of torch.linalg.qr and will be removed in a future PyTorch release.
The boolean parameter 'some' has been replaced with a string parameter 'mode'.
Q, R = torch.qr(A, some)
should be replaced with
Q, R = torch.linalg.qr(A, 'reduced' if some else 'complete') (Triggered internally at ../aten/src/ATen/native/BatchLinearAlgebra.cpp:2349.)
  W = torch.qr(torch.FloatTensor(c, c).normal_())[0]
/opt/conda/lib/python3.8/site-packages/torch/functional.py:1682: UserWarning: torch.lu is deprecated in favor of torch.linalg.lu_factor / torch.linalg.lu_factor_ex and will be removed in a future PyTorch release.
LU, pivots = torch.lu(A, compute_pivots)
should be replaced with
LU, pivots = torch.linalg.lu_factor(A, compute_pivots)
and
LU, pivots, info = torch.lu(A, compute_pivots, get_infos=True)
should be replaced with
LU, pivots, info = torch.linalg.lu_factor_ex(A, compute_pivots) (Triggered internally at ../aten/src/ATen/n

In [4]:
import pandas as pd

pd.read_csv('/usr/src/app/radtts/data/lj_data/LJSpeech-1.1/metadata_formatted.txt', header = None, index_col = None, sep = '|')

0                                                  1  2
0      LJ001-0001.wav  Printing, in the only sense with which we are ...  0
1      LJ001-0002.wav                     in being comparatively modern.  0
2      LJ001-0003.wav  For although the Chinese took impressions from...  0
3      LJ001-0004.wav  produced the block books, which were the immed...  0
4      LJ001-0005.wav  the invention of movable metal letters in the ...  0
...               ...                                                ... ..
13092  LJ050-0274.wav  made certain recommendations which it believes...  0
13093  LJ050-0275.wav  materially improve upon the procedures in effe...  0
13094  LJ050-0276.wav  As has been pointed out, the Commission has no...  0
13095  LJ050-0277.wav  with the active cooperation of the responsible...  0
13096  LJ050-0278.wav  the recommendations we have here suggested wou...  0

[13097 rows x 3 columns]

In [5]:
optimizer = RAdam(model.parameters(), lr=learning_rate,
                      weight_decay=weight_decay)

In [6]:
iteration = 0

scaler = amp.GradScaler(enabled=use_amp)

for param_group in optimizer.param_groups:
    param_group['lr'] = learning_rate

train_loader, valset, collate_fn = prepare_dataloaders(
    data_config, n_gpus, batch_size)

logger = prepare_output_folders_and_logger(output_directory)


initializing training dataloader
['LJ001-0001.wav', 'Printing, in the only sense with which we are at present concerned, differs from most if not from all the arts and crafts represented in the Exhibition', '0']
['LJ001-0002.wav', 'in being comparatively modern.', '0']
['LJ001-0003.wav', 'For although the Chinese took impressions from wood blocks engraved in relief for centuries before the woodcutters of the Netherlands, by a similar process', '0']
['LJ001-0004.wav', 'produced the block books, which were the immediate predecessors of the true printed book,', '0']
['LJ001-0005.wav', 'the invention of movable metal letters in the middle of the fifteenth century may justly be considered as the invention of the art of printing.', '0']
['LJ001-0006.wav', 'And it is worth mention in passing that, as an example of fine typography,', '0']
['LJ001-0007.wav', 'the earliest book printed with movable types, the Gutenberg, or forty-two line Bible of about 1455,', '0']
['LJ001-0008.wav', 'has never 

['LJ016-0140.wav', 'No report of it was made public, as the man was almost immediately recaptured.', '0']
['LJ016-0141.wav', 'He was at work under the supervision of the artisan warder of the prison,', '0']
['LJ016-0142.wav', 'who permitted him to go up on to the roof of the old wards, in order to throw water for flushing purposes down a shoot.', '0']
['LJ016-0143.wav', 'He was out of sight while so employed, and remained so long absent that the warder, becoming uneasy, went in search of him.', '0']
['LJ016-0144.wav', 'He had disappeared.', '0']
['LJ016-0145.wav', 'Encouraged by the shouts and signals of some workmen employed on a building outside, the prisoner made one of the most marvellous jumps on record,', '0']
['LJ016-0146.wav', 'from the building he was on to a distant wall, with a drop of sixty feet between.', '0']
['LJ016-0147.wav', "Then he ran along the coping of the wall towards its angle with Tyler's manufactory, and dropped down on to the gridiron below.", '0']
['LJ016-01

['LJ033-0204.wav', 'So if I found all of these then I would have been able to say these fibers probably had come from this blanket. But since I found so few,', '0']
['LJ033-0205.wav', 'then I would say the possibility exists, these fibers could have come from this blanket, end quote.', '0']
['LJ033-0206.wav', 'Stombaugh confirmed that the rifle could have picked up fibers from the blanket and transferred them to the paper bag.', '0']
['LJ033-0207.wav', 'In light of the other evidence linking Lee Harvey Oswald, the blanket, and the rifle to the paper bag found on the sixth floor,', '0']
['LJ033-0208.wav', "the Commission considered Stombaugh's testimony of probative value in deciding whether Oswald carried the rifle into the building in the paper bag.", '0']
['LJ033-0209.wav', 'The preponderance of the evidence supports the conclusion that Lee Harvey Oswald (1)', '0']
['LJ033-0210.wav', 'told the curtain rod story to Frazier to explain both the return to Irving on a Thursday', '0']
['LJ

Number of speakers: 1
Speaker IDS {'0': 0}
Number of files 13097
Number of files after duration filtering 13097
Dataloader initialized with no augmentations
initializing validation dataloader
['LJ001-0001.wav', 'Printing, in the only sense with which we are at present concerned, differs from most if not from all the arts and crafts represented in the Exhibition', '0']
['LJ001-0002.wav', 'in being comparatively modern.', '0']
['LJ001-0003.wav', 'For although the Chinese took impressions from wood blocks engraved in relief for centuries before the woodcutters of the Netherlands, by a similar process', '0']
['LJ001-0004.wav', 'produced the block books, which were the immediate predecessors of the true printed book,', '0']
['LJ001-0005.wav', 'the invention of movable metal letters in the middle of the fifteenth century may justly be considered as the invention of the art of printing.', '0']
['LJ001-0006.wav', 'And it is worth mention in passing that, as an example of fine typography,', '0'

['LJ005-0031.wav', 'no visiting of friends, no education but religious education, no freedom of diet,', '0']
['LJ005-0032.wav', "no weavers' looms or carpenters' benches. There must be a great deal of solitude, coarse food, a dress of shame,", '0']
['LJ005-0033.wav', 'hard, incessant, irksome, eternal labor, a planned and regulated and unrelenting exclusion of happiness and comfort.', '0']
['LJ005-0034.wav', 'Undeterred by these sarcasms and misrepresentations,', '0']
['LJ005-0035.wav', 'the Society pursued its laudable undertaking with remarkable energy and great singleness of purpose.', '0']
['LJ005-0036.wav', 'The objects it had in view were set forth in one of its earliest meetings.', '0']
['LJ005-0037.wav', 'It sought to obtain and diffuse useful information', '0']
['LJ005-0038.wav', 'to suggest beneficial regulations, and circulate tracts demonstrating the advantages of classification,', '0']
['LJ005-0039.wav', 'constant inspection, regular employment, and humane treatment genera

['LJ018-0265.wav', 'He carried this character with him into penal servitude, and after enduring the full severity of his punishment for several years,', '0']
['LJ018-0266.wav', 'was at length advanced to the comparative ease of a post much coveted by convicts, that of hospital nurse.', '0']
['LJ018-0267.wav', 'His uniform good conduct gained him release from Portland on ticket-of-leave in 1882, just twenty years after his conviction.', '0']
['LJ018-0268.wav', 'A daring and cleverly-planned robbery of diamonds was that of the Tarpeys, man and wife,', '0']
['LJ018-0269.wav', "from an assistant of Loudon and Ryder's, the jewelers in Bond Street. The trick was an old one.", '0']
['LJ018-0270.wav', 'The assistant called with the jewels on approbation at a house specially hired for the purpose in the West End,', '0']
['LJ018-0271.wav', 'and was rendered insensible by chloroform, after which he was bound and the precious stones stolen.', '0']
['LJ018-0272.wav', 'Mrs. Tarpey was almost immedia

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [7]:

prepare_model_weights(model, unfreeze_modules)
model.train()

epoch_offset = 0

Training everything


In [8]:
# ================ MAIN TRAINNIG LOOP! ===================
for epoch in range(epoch_offset, epochs):
    print("Epoch: {}".format(epoch))
    for i, batch in enumerate(train_loader):
        print(i)
        tic = timer()
        model.zero_grad()
        (mel, speaker_ids, text, in_lens, out_lens, attn_prior,
         f0, voiced_mask, p_voiced, energy_avg,
         audiopaths) = parse_data_from_batch(batch)

        if iteration >= binarization_start_iter:
            binarize = True   # binarization training phase
        else:
            binarize = False  # no binarization, soft alignments only

        with amp.autocast(use_amp):
            outputs = model(
                mel, speaker_ids, text, in_lens, out_lens,
                binarize_attention=binarize, attn_prior=attn_prior,
                f0=f0, energy_avg=energy_avg,
                voiced_mask=voiced_mask, p_voiced=p_voiced)
            loss_outputs = criterion(outputs, in_lens, out_lens)

            loss = None
            for k, (v, w) in loss_outputs.items():
                if w > 0:
                    loss = v * w if loss is None else loss + v * w

            w_bin = criterion.loss_weights.get('binarization_loss_weight', 1.0)
            if binarize and iteration >= kl_loss_start_iter:
                binarization_loss = attention_kl_loss(
                    outputs['attn'], outputs['attn_soft'])
                loss += binarization_loss * w_bin
            else:
                binarization_loss = torch.zeros_like(loss)
            loss_outputs['binarization_loss'] = (binarization_loss, w_bin)

        scaler.scale(loss).backward()
        if grad_clip_val > 0:
            scaler.unscale_(optimizer)
            torch.nn.utils.clip_grad_norm_(
                model.parameters(), grad_clip_val)
        scaler.step(optimizer)
        scaler.update()

        toc = timer()
        current_lr = optimizer.param_groups[0]['lr']
        print_list = ["iter: {}  ({:.2f} s)  |  lr: {}".format(
            iteration, toc-tic, current_lr)]

        for k, (v, w) in loss_outputs.items():
            reduced_v = reduce_tensor(v, n_gpus, 0).item()
            loss_outputs[k] = reduced_v
            if rank == 0:
                print_list.append('  |  {}: {:.3f}'.format(k, v))
                logger.add_scalar('train/'+k, reduced_v, iteration)

        if rank == 0:
            print(''.join(print_list), flush=True)

        if iteration > -1 and iteration % iters_per_checkpoint == 0:

            val_loss_outputs = compute_validation_loss(
                iteration, model, criterion, valset, collate_fn,
                batch_size, n_gpus, logger=logger,
                train_config=train_config)
            checkpoint_path = "{}/model_{}".format(
                output_directory, iteration)
            save_checkpoint(model, optimizer, learning_rate, iteration,
                            checkpoint_path)
            print('Validation loss:', val_loss_outputs)


        iteration += 1

# train(n_gpus, rank, **train_config)

Epoch: 0
Everywhere the valley is dotted with the mounds of buried cities carefully guarding the secrets of the centuries of long ago.There had been a pause in legislation, except of a permissive kind. The 2nd and 3rd Victoria, cap. 56or crank visitors and furnished reports concerning any assassination or attempted assassination of a ruler or other major official anywhere in the world.For a second or two the body hung motionless, then, with a strength that astonished the attendant officials,


whereupon they withdrew within their defenses.You could have picked him out without identifying him by just listening to him.


But, fortunately for him, just at the last moment Calcraft was set free.
neither of these slow elevators could have descended from the fifth to the second floor. Furthermore, no elevator was at the second floor when they arrived there.
and not to his race.
The bag found on the sixth floor was 88 inches long.
In evaluating the evidence that Oswald was at the southeast cor

to have made more vigorous efforts to locate Oswald's roominghouse address in Dallas and to interview him regarding these unresolved matters.


/opt/conda/lib/python3.8/site-packages/torch/nn/modules/rnn.py:777: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters(). (Triggered internally at ../aten/src/ATen/native/cudnn/RNN.cpp:968.)
  result = _VF.lstm(input, batch_sizes, hx, self._flat_weights, self.bias,


The direful suspicions which surrounded the case filled the whole country with uneasiness and misgiving,Within a minute after Baker and Truly left Oswald in the lunchroom, Mrs. R. A. Reid, clerical supervisor for the Texas School Book Depository,

Other changes affecting the condition and proper treatment of prisoners were not made until the inspector had urged and recommended them.
iter: 0  (1.51 s)  |  lr: 0.0001  |  loss_mel: 0.520  |  loss_prior_mel: 0.520  |  loss_ctc: 3.745  |  binarization_loss: 0.000


/usr/src/app/radtts/radam.py:76: UserWarning: This overload of addcmul_ is deprecated:
	addcmul_(Number value, Tensor tensor1, Tensor tensor2)
Consider using one of the following signatures instead:
	addcmul_(Tensor tensor1, Tensor tensor2, *, Number value) (Triggered internally at ../torch/csrc/utils/python_arg_parser.cpp:1420.)
  exp_avg_sq.mul_(beta2).addcmul_(1 - beta2, grad, grad)


It is good to know that movements in support of fair play for Cuba has developed in New Orleans as well as in other cities.
the beloved of Nabu, the arbiter, the possessor of wisdom, who seeks out the path of their divinity,thereby leaving a time span of 4.8 to 5.6 seconds between the two shots which struck their mark.

Williams concealed himself behind a chimney till she had re-entered her garret,Oswald's political activities after his return to the United States center around his interest in Cuba and in the Fair Play for Cuba Committee.

elucidated all dark and uncertain points in connection with the crime.A crowd as great as any known collected in the Old Bailey to see the ceremony, about which there were some peculiar features worth recording.

the earliest book printed with movable types, the Gutenberg, or forty-two line Bible of about 1455,Printing, in the only sense with which we are at present concerned, differs from most if not from all the arts and crafts represented in the E

which was generally more formally Gothic than the printing of the German workmen,These and similar founts, cast by the above firm and others,

were the leaders in this luckless change, though our own Baskerville, who was at work some years before them, went much on the same lines;
In spite, however, of his praiseworthy efforts, printing had still one last degradation to undergo.
have now come into general use and are obviously a great improvement on the ordinary modern style in use in England, which is in fact the Bodoni typemany of whose types, indeed, like that of the Subiaco works, are of a transitional character.

and things got worse and worse through the whole of the seventeenth century, so that in the eighteenth printing was very miserably performed.
and was used there with very little variation all through the sixteenth and seventeenth centuries, and indeed into the eighteenth.they must be considered to have ended the age of fine printing in Italy.

and are worthy representativ

In [7]:
from torch.utils.data import DataLoader

In [8]:
val_sampler = None
val_loader = DataLoader(valset, sampler=val_sampler, num_workers=8,
                        shuffle=False, batch_size=batch_size,
                        pin_memory=False, collate_fn=collate_fn)
for i, batch in enumerate(val_loader):
    print(i)
# parse_data_from_batch(val_loader)

than in the same operations with ugly ones.the earliest book printed with movable types, the Gutenberg, or forty-two line Bible of about 1455,Printing, in the only sense with which we are at present concerned, differs from most if not from all the arts and crafts represented in the Exhibition
and which developed more completely and satisfactorily on the side of the lower-case than the capital letters;imitates a much freer hand, simpler, rounder, and less spiky, and therefore far pleasanter and easier to read.

In 1465 Sweynheim and Pannartz began printing in the monastery of Subiaco near Rome,

and the next year Gunther Zeiner at Augsburg followed suit;

A further development of the Roman letter took place at Venice.
And it was a matter of course that in the Middle Ages, when the craftsmen took care that beautiful form should always be a part of their productions whatever they were,
the lower-case being in fact invented in the early Middle Ages.while in 1470 at Paris Udalric Gering and

Most of Caxton's own types are of an earlier character, though they also much resemble Flemish or Cologne letter.
The seventeenth century founts were bad rather negatively than positively.
This was notably the case with the early works printed at Ulm, and in a somewhat lesser degree at Augsburg.
they must be considered to have ended the age of fine printing in Italy.have now come into general use and are obviously a great improvement on the ordinary modern style in use in England, which is in fact the Bodoni type

but his letters, though uninteresting and poor, are not nearly so gross and vulgar as those of either the Italian or the Frenchman.
In England about this time, an attempt was made (notably by Caslon, who started business in London as a type-founder in 1720)
After the end of the fifteenth century the degradation of printing, especially in Germany and Italy,But for the beauty of the earlier work they might have seemed tolerable.

It must be understood that through the whole of 

all books might be at least comely and well-looking: and if to these good qualities were added really beautiful ornament and pictures,
The new jail fell as far short of the demands made on it as did the old.
Here once more the almost invariable modern practice is in opposition to a natural sense of proportion.is the habit that publishers have of eking out a thin volume by printing it on thick paper almost of the substance of cardboard,

the result as measured by the eye being that the lower margin is less than the top one, and that the whole opening has an upside-down look vertically
so that if the two are helpful to one another it is a mere matter of accident.
The paper that is used for ordinary books is exceedingly bad even in this country, but is beaten in the race for vileness
The ornamentation of printed books is too wide a subject to be dealt with fully here; but one thing must be said on it.
The prison population fluctuated a great deal,
printed books might once again illustrate

to which access was granted rarely and as a great favor. But they were allowed the luxury of drink -- if they could pay for it.
The long narrow yard still remained as we saw it in Jacobite times,
they were lighted by a double-grated window two feet nine inches by fourteen inches; and in the doors, which were four inches thick,
There were nine wards in all on the female side, one of them in the attic,
and who are therefore lodged apart from all other districts of the jail. End quote.The middle yard was at first given up to the least heinous offenders. After 1812 it changed functions with the chapel yard.

and beyond it was now a day room for the capital convicts or those awaiting execution.These wards were all fitted with barrack-beds, but no bedding was supplied.

A recent reform had closed the tap kept by the jailer within the precincts, but
to the various wards their friends occupied.
with four casements and two fireplaces, being allotted for a female infirmaryThe state side containe

The boy declared he saw no one, and accordingly passed through without paying the toll of a penny.
Neild gives a list of the various items charged upon a debt of £10, which included instructions to sue,
Bird was, however, discharged within three days by a subscription raised among his fellow-prisoners.and imprisonment for debt has almost entirely disappeared.

watch all night. Adjoining the felons' side lodge is the keeper's office, where the prison books are kept, and his clerk,
the Fleet, and the Marshalsea prisons especially devoted to them,
For this he was summoned before a magistrate, and sentenced as already stated.
The foregoing rentals and payments for privileges, together with fees exacted on commitment and discharge, went to the marshal or keeper of the prison,
Mr. Buxton, in his Inquiry into the System of Prison Discipline,whilst Ludgate, the Giltspur Street, and Borough Compters also received them

Other cases are recorded elsewhere, as at the Giltspur Street Compter, where

...

Sometimes the report was delayed.Those who sat in it were visible to the whole congregation, and still more to the ordinary,Before sentence a prisoner has only to observe the regulations of the jail in order to remain neglected and unnoticed.
they never ceased cursing until the passion of anger so excited was exchanged for joy in some and grief in others.


This was noticeable with Fauntleroy, who, on account of his birth and antecedents, was allowed to occupy a turnkey's room,The ordinary observes him, looks to the sheriffs, and says aloud, 'The service for the dead!'
On one occasion, Mr. Wakefield tells us, the Recorder, who had attended the council at Windsor, did not deliver the report till the following day.

For this the chaplain was a few days later summoned before the jail committee of aldermen,
The Chronicles of Newgate, Volume 2. By Arthur Griffiths. Section 12: Executions, part two.
whose desk and pulpit were just in front of the condemned pew, and within a couple of yards o

the condemned returning to the cells: the forger carried by turnkeys; the youth sobbing aloud convulsively, as a passionate child;
which he has bitten unconsciously, or from rage, or to rouse his fainting courage.
For a while the preacher addresses himself to the congregation at large, who listen attentively
for all thy goodness and loving-kindness to us, and to all men;
The keeper tries to appear unmoved, but his eye wanders anxiously over the combustible assembly.
The poor sheep-stealer is in a frenzy.
move with a quick, jerking motion, not naturally, but, as it were, like the affected parts of a galvanized corpse.
except the clergyman and the burglar, the former of whom is still rolled up at the bottom of the condemned pew,
Let us pass on.
the burglar muttering curses and savage expressions of defiance; whilst the poor sheep-stealer shakes hands with the turnkeys,He throws his hands far from him, and shouts aloud, 'Mercy, good Lord! mercy is all I ask. The Lord in His mercy come!

A

But what are the feelings of those who take part in it?of people who had died friendless, would voluntarily surrender them for the advancement of medical science.

Persons were still living in 1855 who had witnessed dissections at Hicks' Hall, and
Although this misapplication of religious services still went on,to fifty-six in 1839.

All the shops in the neighborhood were shut, and the windows and tops of the houses were crowded with spectators.
parish officers, peace officers, the high constable of the county of Middlesex on horseback, and then the body of Williams,Pennant speaks of Surgeons' Hall as a handsome building, ornamented with Ionic pilasters, and with a double flight of steps to the first floor.Another brutal practice had nearly disappeared about the time of the abolition of dissection. This was the public exhibition of the body,


were publicly exposed in a stable in Little Bridge Street, near Apothecaries' Hall,
Gradually the application of capital punishment became more 

On the scaffold he made a violent attempt to loosen his bonds, and succeeded in getting his hands free.
but not before the greatest scandal had been caused by the unseemly proceedings of the crowd that flocked to see the sight. A sort of fair was held,
but it was actually tried in two provincial towns, Leicester and Durham.
However, the ceremony went forward, and when the signal was given the drop sank.
They were taken back to jail, and were again brought out in the afternoon, by which time fresh and stronger ropes had been procured,
One of the turnkeys rushed forward and pushed him off.
Then with a strong effort he pushed off the white cap, and tried to liberate his neck from the halter, which by this time had been adjusted.He was always known as a mild-mannered man of simple tastes, much given to angling in the New River, and a devoted rabbit fancier.
taking in preference those which are typical and invested with peculiar interest. It is somewhat remarkable that a marked change soon 

KeyboardInterrupt: 

In [ ]:
2+2

In [38]:
for i in range(4600,1000000): #4100
    print(i)
    valset.__getitem__(i)

4600
I have no idea who the sheriffs will get to do the work after me, said Foxen, adding that his assistant, Tom Cheshire,
682
4601
was given to drink, and not to be trusted.
256
4602
I think I could do that sort of job, said Calcraft, on the spur of the moment.
403
4603
Foxen asked him his name and address, and went away.
285
4604
Calcraft thought no more of what had occurred till the next sessions at the Old Bailey, when the sheriffs sent for him,
591
4605
and offered him the post of executioner for the city of London and Middlesex.
390
4606
He accepted, having at first Tom Cheshire as his assistant, then for a time, when Cheshire was dismissed for drunkenness, a man named Osborne.
869
4607
After that he worked alone.
179
4608
I cannot find that Calcraft was sworn in when appointed, or any exact information when the old forbidding ceremony ceased to be practiced.
775
4609
It was customary to make the executioner take the Bible in his hand, and swear solemnly that he would dispatch e

4695
This was presently superseded by a fresh catch --
274
4696
Müller, Müller, He's the man, till a diversion was created by the appearance of the gallows, which was received with continuous yells.
795
4697
As day broke the character of the crowd was betrayed.
311
4698
There were but few women, except of the most degraded sort; the men were mostly young men --
535
4699
sharpers, thieves, gamblers, betting men, the outsiders of the boxing ring,
527
4700
bricklayers' laborers, dock workmen, German artisans and sugar-bakers
479
4701
with the rakings of cheap singing-halls and billiard-rooms, the fast young men of London.
457
4702
But all, whether young or old, men or women, seemed to know nothing, feel nothing, to have no object but the gallows, and to laugh,
861
4703
curse, or shout, as in this heaving and struggling forward they gained or lost in their strong efforts to get nearer where Müller was to die.
789
4704
The actual execution made some impression.
232
4705
The crowd was for a 

4772
Moreover, after the execution, under the old system, the latter had only to receive the body for burial after it had been cut down by the hangman,
789
4773
and placed decently in a shell by the workmen who removed the gallows.
385
4774
Under the new system the whole of the arrangements from first to last fell upon the officers.
533
4775
It was they who formed the chief part of the small select group of spectators;
465
4776
upon them devolved the painful duty of cutting down the body and preparing for the inquest.
528
4777
All that the hangman, whoever he may be, does under the new regime is to unhook the halter and remove the pinioning straps.
810
4778
The interment in a shell filled with quicklime in the passage-way leading to the Old Bailey is also a part of the duty of the prison officials.
744
4779
and for the greater security of prisoners it is roofed in with iron bars which gives it, at least overhead, the aspect of a huge cage.
815
4780
Underfoot and upon the walls roughly 

4843
that the convict's clothes were still the executioner's perquisite.
391
4844
Often the convicts give way to despair. They are too closely watched to be allowed to do themselves much mischief, or suicides would probably be more frequent.
846
4845
But it is neither easy to obtain the instruments of self-destruction nor to elude the vigilance of their guard.
569
4846
The man, Bousfield, however, whose execution was so sadly bungled,
422
4847
made a determined effort to burn himself to death by throwing himself bodily on to the fire in the condemned ward.
613
4848
He was promptly rescued from his perilous condition, but not before his face and hands were badly scorched.
572
4849
They were still much swollen when he was led out to execution.
313
4850
Miller, the Chelsea murderer, who packed his victim's body in a box, and tried to send it by parcels delivery, tried to kill himself,
731
4851
but ineffectively, by running his head against his cell wall.
321
4852
The Chronicles of Newgate

4920
Originally a doctor in practice at Rugeley, in Staffordshire, he had gradually withdrawn from medicine, and devoted himself to the turf;
810
4921
but his sporting operations did not prosper, and he became a needy man, always driven to desperate straits for cash.
699
4922
To meet his liabilities, he raised large sums on forged bills of acceptance drawn upon his mother, a woman of some means,
763
4923
whose signature he counterfeited.
159
4924
In 1854 he owed a very large sum of money, but he was temporarily relieved by the death of his wife,
702
4925
whose life he had insured for £13,000.
329
4926
There is every reason to suppose that he poisoned his wife to obtain possession of this sum upon her death.
516
4927
His brother was supposed to have been his next victim, upon whose life he had also effected an insurance for another £13,000.
792
4928
The brother too died conveniently, but the life office took some exception to the manner of the death, and hesitated to disburse the funds 

...

12810
Pending any such determination, however, this Commission is convinced of the necessity of better coordination
619
12811
and direction of the activities of all existing agencies of Government which are in a position to and do, furnish information
655
12812
and services related to the security of the President.
277
12813
The Commission feels the Secret Service and the FBI, as well as the State Department and the CIA when the President travels abroad,
678
12814
could improve their existing capacities and procedures so as to lessen the chances of assassination.
538
12815
Without, therefore, coming to final conclusions respecting the long-range organization of the President's security,
551
12816
the Commission believes that the facts of the assassination of President Kennedy point to certain measures which,
533
12817
while assuming no radical relocation of responsibilities,
329
12818
can and should be recommended by this Commission in the interest of the more efficient protection of t

12887
the Secret Service had received from the FBI some 9,000 reports on members of the Communist Party.
599
12888
The FBI now transmits information on all defectors, a category which would, of course, have included Oswald.
673
12889
Both Director Hoover and Belmont expressed to the Commission the great concern of the FBI, which is shared by the Secret Service,
773
12890
that referrals to the Secret Service under the new criteria might, if not properly handled,
525
12891
result in some degree of interference with the personal liberty of those involved.
418
12892
They emphasized the necessity that the information now being furnished be handled with judgment and care.
595
12893
The Commission shares this concern.
170
12894
The problem is aggravated by the necessity that the Service obtain the assistance of local law enforcement officials in evaluating the information which it receives
848
12895
and in taking preventive steps.
194
12896
In June 1964, the Secret Service sent to a number of

12969
it makes no use of the recent developments in automatic data processing which are widely used in the business world and in other Government offices.
799
12970
The Secret Service and the Department of the Treasury now recognize this critical need.
404
12971
In the planning document currently under review by the Bureau of the Budget, the Department recommends that it be permitted to hire five qualified persons, quote,
810
12972
to plan and develop a workable and efficient automated file and retrieval system, end quote.
496
12973
Also the Department requests the sum of $100,000 to conduct a detailed feasibility study;
606
12974
this money would be used to compensate consultants, to lease standard equipment or to purchase specially designed pilot equipment.
739
12975
On the basis of such a feasibility study,
211
12976
the Department hopes to design a practical system which will fully meet the needs of the Protective Research Section of the Secret Service.
680
12977
The Commission rec

13042
145 are proposed for the field offices to handle the increased volume of security investigations
577
13043
and be available to protect the President or Vice President when they travel;
370
13044
18 agents are proposed for a rotating pool which will go through an intensive training cycle and also be available to supplement the White House detail
813
13045
in case of unexpected need; and 25 additional agents are recommended to provide the Vice President full protection.
680
13046
The Commission urges that the Bureau of the Budget review these recommendations with the Secret Service and authorize a request for the necessary supplemental appropriation,
844
13047
as soon as it can be justified. The Congress has often stressed that it will support any reasonable request for funds for the protection of the President.
811
13048
Manpower and Technical Assistance From Other Agencies
299
13049
Before the assassination the Secret Service infrequently requested other Federal law enforcement a

IndexError: list index out of range

In [25]:
valset.__getitem__(4693)

Then one struck up the hymn of the Promised Land, and the refrain was at once taken up with a mighty chorus --
614
> /usr/src/app/radtts/data.py(385)__getitem__()
    383         import pdb
    384         pdb.set_trace()
--> 385         attn_prior = self.get_attention_prior(
    386                 text_encoded.shape[0], mel.shape[1])
    387 

ipdb> next
> /usr/src/app/radtts/data.py(386)__getitem__()
    384         pdb.set_trace()
    385         attn_prior = self.get_attention_prior(
--> 386                 text_encoded.shape[0], mel.shape[1])
    387 
    388         if not self.use_attn_prior_masking:

ipdb> next
> /usr/src/app/radtts/data.py(385)__getitem__()
    383         import pdb
    384         pdb.set_trace()
--> 385         attn_prior = self.get_attention_prior(
    386                 text_encoded.shape[0], mel.shape[1])
    387 

ipdb> next
EOFError: Ran out of input
> /usr/src/app/radtts/data.py(385)__getitem__()
    383         import pdb
    384         pdb.set_tr

EOFError: Ran out of input

In [23]:
# text = "1807, through the exertions of the keeper of the jail, spent in the purchase of necessaries."
text = "Then one struck up the hymn of the Promised Land, and the refrain was at once taken up with a mighty chorus --"
text_encoded = valset.get_text(text)

In [36]:
attn_prior = valset.get_attention_prior(
        text_encoded.shape[0], 614)

In [ ]:
def get_attention_prior(self, n_tokens, n_frames):
    # cache the entire attn_prior by filename
    if self.use_attn_prior_masking:
        filename = "{}_{}".format(n_tokens, n_frames)
        prior_path = os.path.join(self.betabinom_cache_path, filename)
        prior_path += "_prior.pth"
        if self.lmdb_cache_path != "":
            attn_prior = pkl.loads(
                self.cache_data_lmdb.get(prior_path.encode('ascii')))
        elif os.path.exists(prior_path):
            attn_prior = torch.load(prior_path)
        else:
            attn_prior = beta_binomial_prior_distribution(
                n_tokens, n_frames, self.betabinom_scaling_factor)
            torch.save(attn_prior, prior_path)
    else:
        attn_prior = torch.ones(n_frames, n_tokens)  # all ones baseline

    return attn_prior

In [31]:
n_tokens = text_encoded.shape[0]
n_frames = 614
filename = "{}_{}".format(n_tokens, n_frames)
prior_path = os.path.join(valset.betabinom_cache_path, filename)
prior_path += "_prior.pth"
os.path.exists(prior_path)

True

In [32]:
attn_prior = torch.load(prior_path)

EOFError: Ran out of input

In [33]:
prior_path

'data_cache/104_614_prior.pth'

In [35]:
attn_prior = torch.load('data_cache/104_614_prior.pth')

EOFError: Ran out of input

In [28]:
valset.lmdb_cache_path

''

In [16]:
next(enumerate(val_loader))

(0,
 {'mel': tensor([[[-2.2227, -1.3934, -0.6888,  ..., -1.0453, -1.0254,  0.0000],
           [-1.4229, -1.1627, -0.4016,  ..., -1.1399, -0.7621,  0.0000],
           [-1.0582, -0.5002, -0.0665,  ..., -0.7611, -0.7377,  0.0000],
           ...,
           [-2.2224, -0.2009,  0.0935,  ..., -1.8294, -1.7082,  0.0000],
           [-2.2018,  0.3467,  0.7160,  ..., -1.7489, -1.7774,  0.0000],
           [-2.2236, -0.0487,  0.2467,  ..., -1.9408, -1.9680,  0.0000]],
  
          [[-1.5247, -1.3842, -1.5710,  ..., -0.9769, -1.0004, -0.5070],
           [-1.0015, -0.9680, -1.0484,  ..., -0.8316, -0.9279, -0.5126],
           [-0.3150, -0.4514, -0.6081,  ..., -0.6470, -0.7730, -0.8672],
           ...,
           [ 0.0932,  0.3096,  0.1344,  ..., -0.4870, -0.7038, -0.9100],
           [ 0.3138,  0.4884,  0.2623,  ..., -0.4786, -0.6557, -0.7978],
           [ 0.1786,  0.4464,  0.3493,  ..., -1.1532, -1.1773, -1.2771]],
  
          [[-1.8418, -0.4860, -0.2918,  ...,  0.0000,  0.0000,  0.0000],


In [ ]:

# if __name__ == "__main__":
# parser = argparse.ArgumentParser()
# parser.add_argument('-c', '--config', type=str,
#                     help='JSON file for configuration')
# parser.add_argument('-p', '--params', nargs='+', default=[])
# args = parser.parse_args()
# args.rank = 0

# # Parse configs.  Globals nicer in this case
# with open(args.config) as f:
#     data = f.read()

# global config
# config = json.loads(data)
# update_params(config, args.params)
# print(config)

# train_config = config["train_config"]
# global data_config
# data_config = config["data_config"]
# global dist_config
# dist_config = config["dist_config"]
# global model_config
# model_config = config["model_config"]


# # make sure we have enough augmentation dimensions
# if 'n_aug_dims' in model_config.keys() and \
#     'aug_probabilities' in data_config.keys():
#     assert(model_config['n_aug_dims'] >= len(data_config['aug_probabilities']))
# # Make sure the launcher sets `RANK` and `WORLD_SIZE`.
# rank = int(os.getenv('RANK', '0'))
# n_gpus = int(os.getenv("WORLD_SIZE", '1'))
# print('> got rank {} and world size {} ...'.format(rank, n_gpus))

# if n_gpus == 1 and rank != 0:
#     raise Exception("Doing single GPU training on rank > 0")
